In [97]:
import tushare as ts
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import MySQLdb
import time
import datetime
import warnings
warnings.filterwarnings("ignore")
from imp import reload
import chan_series

In [254]:
db = MySQLdb.connect(host="127.0.0.1",user="sa",passwd="sasasa",db="quant",charset="utf8")
cursor = db.cursor()
sql = "select * from stock_min where ts_code='000425.SZ' and trade_time>'2010-01-01' and trade_time<'2020-01-01' order by trade_time"
df = pd.read_sql(sql,db)
cursor.close()
db.close()
print('data loaded',len(df))
reload(chan_series) #重新加载外部chan.py
df=chan_series.build(df)

data loaded 578535
开始处理： 0 / 578535
开始处理： 10000 / 578535
开始处理： 20000 / 578535
开始处理： 30000 / 578535
开始处理： 40000 / 578535
开始处理： 50000 / 578535
开始处理： 60000 / 578535
开始处理： 70000 / 578535
开始处理： 80000 / 578535
开始处理： 90000 / 578535
开始处理： 100000 / 578535
开始处理： 110000 / 578535
开始处理： 120000 / 578535
开始处理： 130000 / 578535
开始处理： 140000 / 578535
开始处理： 150000 / 578535
开始处理： 160000 / 578535
开始处理： 170000 / 578535
开始处理： 180000 / 578535
开始处理： 190000 / 578535
开始处理： 200000 / 578535
开始处理： 210000 / 578535
开始处理： 220000 / 578535
开始处理： 230000 / 578535
开始处理： 240000 / 578535
开始处理： 250000 / 578535
开始处理： 260000 / 578535
开始处理： 270000 / 578535
开始处理： 280000 / 578535
开始处理： 290000 / 578535
开始处理： 300000 / 578535
开始处理： 310000 / 578535
开始处理： 320000 / 578535
开始处理： 330000 / 578535
开始处理： 340000 / 578535
开始处理： 350000 / 578535
开始处理： 360000 / 578535
开始处理： 370000 / 578535
开始处理： 380000 / 578535
开始处理： 390000 / 578535
开始处理： 400000 / 578535
开始处理： 410000 / 578535
开始处理： 420000 / 578535
开始处理： 430000 / 578535
开始处理： 440000 / 578535
开始处理：

In [265]:
result_df=pd.DataFrame()
qs_mark_df=pd.DataFrame()
zs_no_pre=0
last_zg=0
last_zd=0
last_zsg_gg=0
last_zsg_dd=0
last_zsg_nos=''
last_zsg_dir=''
last_zsg_start_dir=''
last_zsg_end_dir=''
is_merge_last=False
is_buy=False
last_buy_price=0
profit=0
profit_100=100
for n, k in df.loc[(df["line"]=='bottom') | (df["line"]=='top')].iterrows():
    #print(zs_no_pre,k.zs_no,zs_no_pre==0)
    if zs_no_pre!=0 and (k.zs_no==0 or k.zs_no>zs_no_pre): #中枢结束
        #print('中枢结束',zs_no_pre, '合并',is_merge_last)
        last_zsg_end_dir='down' if k.line=='bottom' else 'up'
        #print(last_zsg_start_dir,last_zsg_end_dir,last_zsg_dir,last_zsg_nos)
        if is_merge_last:
            #update last one
            index=len(qs_mark_df)-1
            qs_mark_df.ix[index,'zsg_gg']=last_zsg_gg            
            qs_mark_df.ix[index,'zsg_dd']=last_zsg_dd
            qs_mark_df.ix[index,'zsg_nos']=last_zsg_nos
            qs_mark_df.ix[index,'zsg_end_dir']=last_zsg_end_dir
        else:
            #append to list
            #print(zs_no_pre,k.zs_no)
            qs_mark_df=qs_mark_df.append({'zsg_start_dir':last_zsg_start_dir,'zsg_end_dir':last_zsg_end_dir, 'zsg_dir':last_zsg_dir, 'zsg_gg':last_zsg_gg, 'zsg_dd':last_zsg_dd, 'zsg_nos':last_zsg_nos},ignore_index=True)
        
        last_zs_k=df.loc[0:n].loc[df["zs_no"]>0].iloc[-1] if k.zs_no==0 else df.loc[0:n-1].loc[df["zs_no"]>0].iloc[-1]
        last_zg=last_zs_k.zg
        last_zd=last_zs_k.zd
        #print(last_zs_k.zs_no,last_zg,last_zd)

    if k.zs_no!=0 and (zs_no_pre==0 or k.zs_no>zs_no_pre): #新中枢
        #print('新中枢',k.zs_no,k.zg,k.zd)
        #是否与前面中枢需要合并
        if last_zsg_dd!=0 and last_zsg_gg!=0 and max(last_zsg_dd,k.dd)<min(last_zsg_gg,k.gg):
            #print(last_zsg_gg,last_zsg_dd,k.gg,k.dd)
            last_zsg_gg=max(last_zsg_gg,k.gg)
            last_zsg_dd=min(last_zsg_dd,k.dd)
            last_zsg_nos+=(str(int(k.zs_no))+',')
            is_merge_last=True
        else:
            if last_zsg_dd==0:
                last_zsg_dir=''
            else:
                last_zsg_dir='down' if k.gg<last_zsg_dd else 'up'
            last_zsg_gg=k.gg
            last_zsg_dd=k.dd
            last_zsg_nos=(str(int(k.zs_no))+',')
            last_zsg_start_dir='down' if k.line=='bottom' else 'up'
            is_merge_last=False    
        
#     if is_buy!=True and k.line=='bottom' and len(qs_mark_df)>=2: #找三买
#         k1_dir=qs_mark_df.iloc[-2].zsg_dir
#         k1_start_dir=qs_mark_df.iloc[-2].zsg_start_dir
#         k1_end_dir=qs_mark_df.iloc[-2].zsg_end_dir
#         k2_dir=qs_mark_df.iloc[-1].zsg_dir
#         k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
#         k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
#         k2_gg=qs_mark_df.iloc[-1].zsg_gg            
#         k2_dd=qs_mark_df.iloc[-1].zsg_dd
#         #print(k1_start_dir,k1_end_dir,k2_start_dir,k2_end_dir,k2_dir)
#         #买点形态
#         is_qs_ok=False
#         if k1_start_dir=='down' and k1_end_dir=='down' and k2_start_dir=='down' and k2_end_dir=='down' and k2_dir=='down':
#             is_qs_ok=True
#         if k1_start_dir=='down' and k1_end_dir=='down' and k2_start_dir=='down' and k2_end_dir=='up' and k2_dir=='down':
#             is_qs_ok=True
#         #print('is_qs_ok')
#         if is_qs_ok and k.low>k2_gg: #没有碰到中枢，反弹
#             print('买入',k.close,k.trade_time, k.line, k2_gg, k2_dd)
#             is_buy=True
#             last_buy_price=k.close

    if is_buy!=True and k.line=='bottom' and len(qs_mark_df)>=2: #找买点
        k2_dir=qs_mark_df.iloc[-1].zsg_dir
        k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
        k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
        #print(k1_start_dir,k1_end_dir,k2_start_dir,k2_end_dir,k2_dir)
        #买点形态
        if k2_end_dir=='up' and k.low>last_zg: #没有碰到中枢，反弹
            print('买入',k.close,k.trade_time, k.line)
            is_buy=True
            last_buy_price=k.close
            
    if is_buy and k.line=='top' and len(qs_mark_df)>=2: #找卖点
        k2_dir=qs_mark_df.iloc[-1].zsg_dir
        k2_start_dir=qs_mark_df.iloc[-1].zsg_start_dir
        k2_end_dir=qs_mark_df.iloc[-1].zsg_end_dir
        #print(k1_end_dir,k.high,last_zd)
        #卖点形态
        if k2_end_dir=='down' and k.high<last_zd: #没有碰到中枢zd，下反弹
            #一股变几股
            rate=1
            trade_time=k.trade_time.strftime("%Y-%m-%d %H:%M:%S")
            if trade_time=='2011-03-16 10:04:00':
                rate=2
            elif trade_time=='2015-09-23 10:12:00':
                rate=3
            
            profit+=k.close*rate-last_buy_price
            profit_100=profit_100*(k.close*rate/last_buy_price)
            print('卖出',k.close,'本次获利',k.close*rate-last_buy_price,'总获利',profit,k.trade_time,'100初仓累计：',profit_100)
            is_buy=False
                
    zs_no_pre=k.zs_no

买入 35.48 2010-01-15 09:52:00 bottom
卖出 35.28 本次获利 -0.19999999999999574 总获利 -0.19999999999999574 2010-01-26 13:29:00 100初仓累计： 99.43630214205187
买入 34.98 2010-02-11 13:13:00 bottom
卖出 36.24 本次获利 1.2600000000000051 总获利 1.0600000000000094 2010-03-05 10:15:00 100初仓累计： 103.01805573550486
买入 36.35 2010-03-09 13:34:00 bottom
卖出 35.79 本次获利 -0.5600000000000023 总获利 0.5000000000000071 2010-03-11 11:23:00 100初仓累计： 101.43098252472404
买入 34.91 2010-03-17 14:41:00 bottom
卖出 35.9 本次获利 0.990000000000002 总获利 1.490000000000009 2010-03-25 09:32:00 100初仓累计： 104.30742688735586
买入 36.23 2010-03-26 14:54:00 bottom
卖出 40.75 本次获利 4.520000000000003 总获利 6.010000000000012 2010-04-13 14:36:00 100初仓累计： 117.32066369472126
买入 41.11 2010-04-15 10:24:00 bottom
卖出 41.6 本次获利 0.490000000000002 总获利 6.500000000000014 2010-04-22 13:43:00 100初仓累计： 118.71903696668463
买入 30.5 2010-05-13 10:37:00 bottom
卖出 32.7 本次获利 2.200000000000003 总获利 8.700000000000017 2010-05-17 09:59:00 100初仓累计： 127.28237733805204
买入 33.8 2010-05-20 13:09:00 

卖出 14.7 本次获利 -0.9500000000000011 总获利 23.9 2012-03-26 09:49:00 100初仓累计： 179.53013323941624
买入 13.92 2012-04-05 13:39:00 bottom
卖出 14.48 本次获利 0.5600000000000005 总获利 24.46 2012-04-16 13:58:00 100初仓累计： 186.75260986399047
买入 14.6 2012-04-18 14:12:00 bottom
卖出 14.95 本次获利 0.34999999999999964 总获利 24.810000000000002 2012-04-24 14:34:00 100初仓累计： 191.22955599086694
买入 15.1 2012-04-26 09:31:00 bottom
卖出 15.52 本次获利 0.41999999999999993 总获利 25.230000000000004 2012-05-07 13:05:00 100初仓累计： 196.54852377339435
买入 14.33 2012-05-17 14:20:00 bottom
卖出 14.56 本次获利 0.23000000000000043 总获利 25.460000000000004 2012-05-25 13:28:00 100初仓累计： 199.70317558552838
买入 15.27 2012-05-28 14:09:00 bottom
卖出 15.58 本次获利 0.3100000000000005 总获利 25.770000000000003 2012-05-30 09:53:00 100初仓累计： 203.75739853454695
买入 15.28 2012-06-01 10:07:00 bottom
卖出 15.0 本次获利 -0.27999999999999936 总获利 25.490000000000002 2012-06-04 10:51:00 100初仓累计： 200.02362421585107
买入 14.69 2012-06-11 14:31:00 bottom
卖出 14.79 本次获利 0.09999999999999964 总获利 25.5900

买入 9.7 2014-11-21 10:47:00 bottom
卖出 10.23 本次获利 0.5300000000000011 总获利 30.149999999999995 2014-11-28 10:29:00 100初仓累计： 344.1651994309272
买入 10.41 2014-12-01 11:12:00 bottom
卖出 13.54 本次获利 3.129999999999999 总获利 33.279999999999994 2014-12-17 11:22:00 100初仓累计： 447.6461863875844
买入 14.07 2014-12-19 11:25:00 bottom
卖出 14.71 本次获利 0.6400000000000006 总获利 33.919999999999995 2014-12-22 14:25:00 100初仓累计： 468.00820197308934
买入 14.79 2014-12-25 10:40:00 bottom
卖出 14.49 本次获利 -0.29999999999999893 总获利 33.62 2015-01-06 10:36:00 100初仓累计： 458.5151349959476
买入 13.18 2015-01-23 10:48:00 bottom
卖出 12.93 本次获利 -0.25 总获利 33.37 2015-01-29 09:55:00 100初仓累计： 449.81795868722327
买入 11.49 2015-02-09 10:20:00 bottom
卖出 13.75 本次获利 2.26 总获利 35.629999999999995 2015-03-04 13:38:00 100初仓累计： 538.2939018232654
买入 13.94 2015-03-10 10:18:00 bottom
卖出 13.85 本次获利 -0.08999999999999986 总获利 35.53999999999999 2015-03-12 14:22:00 100初仓累计： 534.8185466465011
买入 13.98 2015-03-16 09:59:00 bottom
卖出 14.68 本次获利 0.6999999999999993 总获利 36.23

KeyboardInterrupt: 

In [228]:
len(df.loc[(df["line"]=='bottom') | (df["line"]=='top')])

10201

In [215]:
qs_mark_df.loc[0:9]

zsg_dd zsg_dir zsg_end_dir  zsg_gg  \
0   23.61                  up   24.33   
1   24.37      up        down   27.50   
2   24.06    down        down   24.19   
3   21.75    down          up   22.60   
4   20.61    down        down   21.23   
5   19.35    down        down   20.50   
6   17.35    down          up   17.58   
7   18.69      up          up   19.06   
8   19.54      up        down   20.60   
9   12.50    down          up   13.18   

                                             zsg_nos zsg_start_dir  
0                                                 1,            up  
1  2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,18,...            up  
2                                                31,          down  
3                                                31,          down  
4                                                32,          down  
5                                          33,34,35,          down  
6                                                36,          down  
7                                                37,            up  
8                                                38,            up  
9                                          39,40,40,          down

In [70]:
result_df.groupby('direction')['trade_price'].mean()

direction
downdown    13.105517
upup        16.638000
Name: trade_price, dtype: float64

In [255]:
outputpath='E:/jupyter/000425-10Y.csv'
df.to_csv(outputpath,sep=',',index=True,header=True)